# Author: Bosie Akioyamen

This Module ```Model_Selection_Training``` does Modeling and Evaluation:
1. Modeling:
    - SSD
    - Evaluate the models using appropriate metrics (e.g., accuracy, precision, recall, F1 score, mean average precision for object detection).
    - Document the modeling and evaluation process in a Jupyter Notebook.
3. Deliverables:
    - Jupyter Notebook with modeling and evaluation steps.
    - Summary of model performance and comparison for the business presentation and written report.

In [1]:
!pip install pandas pyyaml torch torchvision numpy pillow scikit-learn ultralytics

In [ ]:
import os
import pandas as pd
import yaml
import torch
import numpy as np
from PIL import Image
from torchvision import transforms
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from ultralytics import YOLO
from collections import defaultdict

# Define the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Paths
project_root = os.path.abspath(os.path.join(os.getcwd(), '..'))
data_dir = os.path.join(project_root, 'data')
image_dir = os.path.join(data_dir, 'downloaded_images', 'images')
label_file = os.path.join(data_dir, 'labels.csv')
label_dir = os.path.join(data_dir, 'downloaded_images', 'labels')

# Ensure label directory exists
os.makedirs(label_dir, exist_ok=True)

print("Reading labels...")
df = pd.read_csv(label_file)
print("Initial labels dataframe loaded.")
print(f"Original DataFrame length: {len(df)}")


# Verify all images exist
df = df[df['frame'].apply(lambda x: os.path.exists(os.path.join(image_dir, x)))]
print(f"DataFrame length after verifying image paths: {len(df)}")

# Print unique class IDs to verify they are within the expected range
unique_class_ids = df['class_id'].unique()
print("Unique class IDs:", unique_class_ids)

# Check if any class IDs are out of bounds
nc = 6  # Number of classes
if any(unique_class_id >= nc or unique_class_id < 0 for unique_class_id in unique_class_ids):
    print(f"Error: Found class IDs out of range [0, {nc-1}]. Please fix the labels.")
else:
    print(f"All class IDs are within the range [0, {nc-1}].")

# Generate YOLO-format label files
def create_yolo_labels(df, label_dir, image_dir):
    for idx, row in df.iterrows():
        img_path = os.path.join(image_dir, row['frame'])
        if os.path.exists(img_path):
            img = Image.open(img_path)
            w, h = img.size
            yolo_bbox = [
                row['class_id'],
                (row['xmin'] + row['xmax']) / 2 / w,
                (row['ymin'] + row['ymax']) / 2 / h,
                (row['xmax'] - row['xmin']) / w,
                (row['ymax'] - row['ymin']) / h
            ]
            label_path = os.path.join(label_dir, os.path.splitext(row['frame'])[0] + '.txt')
            with open(label_path, 'a') as f:
                f.write(" ".join(map(str, yolo_bbox)) + '\n')

print("Creating YOLO-format label files...")
create_yolo_labels(df, label_dir, image_dir)

# Verify label files
print(f"Created label files in {label_dir}")
sample_label_file = os.listdir(label_dir)[0]
with open(os.path.join(label_dir, sample_label_file), 'r') as f:
    print(f"Sample label file ({sample_label_file}):\n{f.read()}")

# Class names
class_names = ['car', 'truck', 'pedestrian', 'bicyclist', 'light', 'unknown']

# Create the YAML configuration file dynamically
config = {
    'path': data_dir,
    'train': os.path.relpath(image_dir, data_dir),
    'val': os.path.relpath(image_dir, data_dir),
    'nc': len(class_names),
    'names': class_names
}

config_file = os.path.join(data_dir, 'custom_dataset.yaml')
with open(config_file, 'w') as file:
    yaml.dump(config, file, default_flow_style=False)

print(f"YAML configuration file created at {config_file}")

print("Reading labels...")
df = pd.read_csv(label_file)
print("Initial labels dataframe loaded.")
print(f"Original DataFrame length: {len(df)}")

# Verify all images exist
df = df[df['frame'].apply(lambda x: os.path.exists(os.path.join(image_dir, x)))]
print(f"DataFrame length after verifying image paths: {len(df)}")

df = df.sample(frac=1).reset_index(drop=True)

# Split the DataFrame into halves three times
for i in range(10):
    df = df[:len(df)//2]
    print(f"DataFrame length after split {i+1}: {len(df)}")

print("Final truncated DataFrame length:", len(df))

# Print out the first few rows to check the labels
print("Sample labels:")
print(df.head())

# Split the DataFrame into train and val sets
train_frames, val_frames = train_test_split(df.frame.unique(), test_size=0.1, random_state=99)
df_train, df_val = df[df['frame'].isin(train_frames)], df[df['frame'].isin(val_frames)]

# Normalize bounding boxes (assuming coordinates are in pixels)
def normalize_bbox(df, image_dir):
    df = df.copy()
    df['xmin'] = df['xmin'].astype(float)
    df['xmax'] = df['xmax'].astype(float)
    df['ymin'] = df['ymin'].astype(float)
    df['ymax'] = df['ymax'].astype(float)
    for idx, row in df.iterrows():
        img_path = os.path.join(image_dir, row['frame'])
        if os.path.exists(img_path):
            img = Image.open(img_path)
            w, h = img.size
            df.at[idx, 'xmin'] /= w
            df.at[idx, 'xmax'] /= w
            df.at[idx, 'ymin'] /= h
            df.at[idx, 'ymax'] /= h
        else:
            print(f"Image {img_path} not found.")
            df.drop(idx, inplace=True)
    return df

print("Calling normalize Bounding Boxes...")
df_train = normalize_bbox(df_train, image_dir)
df_val = normalize_bbox(df_val, image_dir)

# Print out the first few rows of normalized labels to check
print("Sample normalized labels (train):")
print(df_train.head())

print("Sample normalized labels (val):")
print(df_val.head())

class SelfDrivingCarDataset(Dataset):
    def __init__(self, df, image_dir, transform=None):
        self.df = df
        self.image_dir = image_dir
        self.transform = transform
        self.image_infos = df.frame.unique()
        print(f"Dataset initialized with {len(self.image_infos)} images.")

    def __len__(self):
        return len(self.image_infos)

    def __getitem__(self, idx):
        img_id = self.image_infos[idx]
        img_path = os.path.join(self.image_dir, img_id)
        if not os.path.exists(img_path):
            print(f"Image {img_path} not found.")
            return None, None
        img = Image.open(img_path).convert('RGB')
        if self.transform:
            img = self.transform(img)
        data = self.df[self.df['frame'] == img_id]
        boxes = data[['xmin', 'ymin', 'xmax', 'ymax']].values
        labels = data['class_id'].values
        boxes = torch.as_tensor(boxes, dtype=torch.float32)
        labels = torch.as_tensor(labels, dtype=torch.int64)
        target = {'boxes': boxes, 'labels': labels}
        # Print out the labels and bounding boxes for each image
        print(f"Image ID: {img_id}")
        print(f"Boxes: {boxes}")
        print(f"Labels: {labels}")
        return img, target

transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor()
])

def collate_fn(batch):
    batch = list(filter(lambda x: x[0] is not None, batch))
    return tuple(zip(*batch))

print("Creating Datasets...")
train_ds = SelfDrivingCarDataset(df_train, image_dir, transform)
val_ds = SelfDrivingCarDataset(df_val, image_dir, transform)

print("Loading Datasets...")
train_loader = DataLoader(train_ds, batch_size=10, shuffle=True, collate_fn=collate_fn)
val_loader = DataLoader(val_ds, batch_size=10, shuffle=False, collate_fn=collate_fn)

# Load the YOLO model
yolo_model = YOLO('yolov8m.pt')

# Override the default configuration with the custom dataset
yolo_model.train(data=config_file, epochs=1, batch=10, imgsz=224)

print("Evaluating Models...")

# Function to evaluate model on a batch of images
print("Evaluating Models...")

# Function to evaluate model on a batch of images
def evaluate_model(model, loader, device):
    model.eval()
    results = []
    with torch.no_grad():
        for imgs, targets in loader:
            imgs = [img.to(device) for img in imgs]
            outputs = model.predict(imgs, verbose=False)
            for output in outputs:
                results.append(output)
    return results

print("Move model to device..")
yolo_model.to(device)

def calculate_metrics(results, targets):
    print("Calculating Metrics...")
    # Initialize containers for true positives, false positives, and false negatives
    tp = defaultdict(int)
    fp = defaultdict(int)
    fn = defaultdict(int)

    # Iterate over all results and corresponding targets
    for result, target in zip(results, targets):
        pred_boxes = result.boxes.xyxy.cpu().numpy()
        pred_labels = result.boxes.cls.cpu().numpy()
        pred_scores = result.boxes.conf.cpu().numpy()

        true_boxes = target['boxes'].cpu().numpy()
        true_labels = target['labels'].cpu().numpy()

        for label in set(true_labels).union(set(pred_labels)):
            # Filter predictions and targets by the current label
            pred_indices = pred_labels == label
            true_indices = true_labels == label

            pred_boxes_label = pred_boxes[pred_indices]
            true_boxes_label = true_boxes[true_indices]

            # Calculate the IoU for each predicted and true box pair
            ious = np.zeros((len(pred_boxes_label), len(true_boxes_label)))
            for i, pred_box in enumerate(pred_boxes_label):
                for j, true_box in enumerate(true_boxes_label):
                    ious[i, j] = iou(pred_box, true_box)

            # Determine matches based on IoU threshold
            iou_threshold = 0.5
            matched_pred = set()
            matched_true = set()

            for i, iou_row in enumerate(ious):
                for j, iou_val in enumerate(iou_row):
                    if iou_val >= iou_threshold:
                        matched_pred.add(i)
                        matched_true.add(j)

            # Update counts
            tp[label] += len(matched_pred)
            fp[label] += len(pred_boxes_label) - len(matched_pred)
            fn[label] += len(true_boxes_label) - len(matched_true)

    # Calculate precision, recall, and F1-score for each class
    precisions = {}
    recalls = {}
    f1_scores = {}

    for label in set(tp.keys()).union(fp.keys()).union(fn.keys()):
        precision = tp[label] / (tp[label] + fp[label]) if (tp[label] + fp[label]) > 0 else 0
        recall = tp[label] / (tp[label] + fn[label]) if (tp[label] + fn[label]) > 0 else 0
        f1_score = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0

        precisions[label] = precision
        recalls[label] = recall
        f1_scores[label] = f1_score

    return precisions, recalls, f1_scores

# Define IoU function
def iou(boxA, boxB):
    xA = max(boxA[0], boxB[0])
    yA = max(boxA[1], boxB[1])
    xB = min(boxA[2], boxB[2])
    yB = min(boxA[3], boxB[3])
    interArea = max(0, xB - xA + 1) * max(0, yA - yB + 1)
    boxAArea = (boxA[2] - boxA[0] + 1) * (boxA[3] - boxA[1] + 1)
    boxBArea = (boxB[2] - boxB[0] + 1) * (boxB[3] - boxB[1] + 1)
    iou = interArea / float(boxAArea + boxBArea - interArea)
    return iou

def train_one_epoch(model, optimizer, data_loader, device, epoch, print_freq=10):
    model.train()
    total_loss = 0
    for i, (images, targets) in enumerate(data_loader):
        images = [image.to(device) for image in images]
        targets = [{k: v.to(device) for k, v in t.items()} for t in targets]

        # Clear gradients
        optimizer.zero_grad()

        # Forward pass
        outputs = model(images)
        loss = sum(loss for loss in outputs.values())
        
        # Backward pass
        loss.backward()
        optimizer.step()
        
        total_loss += loss.item()
        
        if i % print_freq == 0:
            print(f'Epoch {epoch}, Batch {i}, Loss: {loss.item()}')

    return total_loss / len(data_loader)

def train_model(model, train_loader, val_loader, device, num_epochs=10, learning_rate=1e-4):
    optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
    
    for epoch in range(num_epochs):
        print(f'Starting epoch {epoch+1}/{num_epochs}')
        train_loss = train_one_epoch(model, optimizer, train_loader, device, epoch)
        print(f'Epoch {epoch+1}, Train Loss: {train_loss}')
        
        if epoch % 1 == 0:  # Change this to 5 or desired value to run validation less frequently
            model.eval()
            results = evaluate_model(model, val_loader, device)
            targets = [{k: v for k, v in t.items()} for _, t in val_loader.dataset]
            precisions, recalls, f1_scores = calculate_metrics(results, targets)
            
            print(f'Epoch {epoch+1}, Validation Metrics:')
            for label in precisions.keys():
                print(f'Class {label}: Precision: {precisions[label]:.4f}, Recall: {recalls[label]:.4f}, F1-Score: {f1_scores[label]:.4f}')

print("Training Model...")
train_model(yolo_model, train_loader, val_loader, device, num_epochs=2)

def display_evaluation_results(results):
    for i, result in enumerate(results):
        print(f"Image {i+1}")
        for box in result.boxes:
            label = result.names[box.cls.item()]
            coordinates = box.xyxy.tolist()
            confidence = round(box.conf.item(), 2)
            print(f"Label: {label}, Confidence: {confidence}, Coordinates: {coordinates}")

print("Evaluate the model on the validation set...")
results = evaluate_model(yolo_model, val_loader, device)

print("Display evaluation results..")
display_evaluation_results(results)

/usr/local/lib/python3.11/site-packages/threadpoolctl.py:1010: RuntimeWarning: 
Found Intel OpenMP ('libiomp') and LLVM OpenMP ('libomp') loaded at
the same time. Both libraries are known to be incompatible and this
can cause random crashes or deadlocks on Linux when loaded in the
same Python program.
Using threadpoolctl may cause crashes or deadlocks. For more
information and possible workarounds, please see
    https://github.com/joblib/threadpoolctl/blob/master/multiple_openmp.md

  warnings.warn(msg, RuntimeWarning)


Reading labels...
Initial labels dataframe loaded.
Original DataFrame length: 132406
DataFrame length after verifying image paths: 132406
Unique class IDs: [1 3 2 5 4]
All class IDs are within the range [0, 5].
Creating YOLO-format label files...
Created label files in /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/labels
Sample label file (1479504671392444865.txt):
3 0.103125 0.495 0.027083333333333334 0.09666666666666666
3 0.125 0.49333333333333335 0.020833333333333332 0.07333333333333333
1 0.41458333333333336 0.5516666666666666 0.45416666666666666 0.6166666666666667
2 0.759375 0.45 0.3229166666666667 0.24666666666666667
3 0.703125 0.5633333333333334 0.09375 0.26666666666666666
3 0.771875 0.5616666666666666 0.07708333333333334 0.31666666666666665
3 0.8395833333333333 0.5466666666666666 0.1 0.29333333333333333
3 0.9447916666666667 0.49833333333333335 0.027083333333333334 0.09666666666666666
3 0.103125 0.495 0.027083333333333334 0.096666666666666

train: Scanning /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/labels... 18000 images, 4241 backgrounds, 0 corrupt: 100%|██████████| 22241/22241 [00:17<00

train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019952686311006.jpg: 2 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019953180167674.jpg: 1 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019953689774621.jpg: 5 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019954186238236.jpg: 5 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019954685370994.jpg: 4 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019955185244088.jpg: 4 duplicate labels removed
train: WARNING ⚠

train: New cache created: /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/labels.cache


val: Scanning /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/labels.cache... 18000 images, 4241 backgrounds, 0 corrupt: 100%|██████████| 22241/22241 [00:0

train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019952686311006.jpg: 2 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019953180167674.jpg: 1 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019953689774621.jpg: 5 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019954186238236.jpg: 5 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019954685370994.jpg: 4 duplicate labels removed
train: WARNING ⚠️ /Users/obosieakioyamen/USD/AAI510/final_project/objectdetection/data/downloaded_images/images/1478019955185244088.jpg: 4 duplicate labels removed
train: WARNING ⚠

Plotting labels to runs/detect/train10/labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.001, momentum=0.9) with parameter groups 77 weight(decay=0.0), 84 weight(decay=0.00046875), 83 bias(decay=0.0)
TensorBoard: model graph visualization added ✅
Image sizes 224 train, 224 val
Using 0 dataloader workers
Logging results to runs/detect/train10
Starting training for 1 epochs...

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


        1/1         0G      1.739      3.309       1.15         94        224:   3%|▎         | 64/2225 [02:55<1:37:38,  2.71s/it]

In [ ]:
''''
import os
import pandas as pd
import yaml
import torch
import numpy as np
from PIL import Image
from torchvision import transforms
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from ultralytics import YOLO
from collections import defaultdict

# Define the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Paths
project_root = os.path.abspath(os.path.join(os.getcwd(), '..'))
data_dir = os.path.join(project_root, 'data')
image_dir = os.path.join(data_dir, 'downloaded_images', 'images')
label_file = os.path.join(data_dir, 'labels.csv')
label_file_val = os.path.join(data_dir, 'labels_val.csv')

# Class names
class_names = ['car', 'truck', 'pedestrian', 'bicyclist', 'light']

# Create the YAML configuration file dynamically
config = {
    'path': data_dir,
    'train': os.path.relpath(image_dir, data_dir),
    'val': os.path.relpath(image_dir, data_dir),
    'nc': len(class_names),
    'names': class_names
}

config_file = os.path.join(data_dir, 'custom_dataset.yaml')
with open(config_file, 'w') as file:
    yaml.dump(config, file, default_flow_style=False)

print(f"YAML configuration file created at {config_file}")

# Your existing code to load and process the dataset
print("Reading labels...")
df = pd.read_csv(label_file)
print("Initial labels dataframe loaded.")
print(f"Original DataFrame length: {len(df)}")

# Verify all images exist
df = df[df['frame'].apply(lambda x: os.path.exists(os.path.join(image_dir, x)))]
print(f"DataFrame length after verifying image paths: {len(df)}")

# Shuffle the DataFrame
df = df.sample(frac=1).reset_index(drop=True)

# Split the DataFrame into halves three times
for i in range(10):
    df = df[:len(df)//2]
    print(f"DataFrame length after split {i+1}: {len(df)}")

# The DataFrame is now truncated to the last split
print("Final truncated DataFrame length:", len(df))

# Split the DataFrame into train and val sets
train_frames, val_frames = train_test_split(df.frame.unique(), test_size=0.1, random_state=99)
df_train, df_val = df[df['frame'].isin(train_frames)], df[df['frame'].isin(val_frames)]

# Normalize bounding boxes (assuming coordinates are in pixels)
def normalize_bbox(df, image_dir):
    df = df.copy()
    df['xmin'] = df['xmin'].astype(float)
    df['xmax'] = df['xmax'].astype(float)
    df['ymin'] = df['ymin'].astype(float)
    df['ymax'] = df['ymax'].astype(float)
    for idx, row in df.iterrows():
        img_path = os.path.join(image_dir, row['frame'])
        if os.path.exists(img_path):
            img = Image.open(img_path)
            w, h = img.size
            df.at[idx, 'xmin'] /= w
            df.at[idx, 'xmax'] /= w
            df.at[idx, 'ymin'] /= h
            df.at[idx, 'ymax'] /= h
        else:
            print(f"Image {img_path} not found.")
            df.drop(idx, inplace=True)
    return df

print("Calling normalize Bounding Boxes...")
df_train = normalize_bbox(df_train, image_dir)
df_val = normalize_bbox(df_val, image_dir)

class SelfDrivingCarDataset(Dataset):
    def __init__(self, df, image_dir, transform=None):
        self.df = df
        self.image_dir = image_dir
        self.transform = transform
        self.image_infos = df.frame.unique()
        print(f"Dataset initialized with {len(self.image_infos)} images.")

    def __len__(self):
        return len(self.image_infos)

    def __getitem__(self, idx):
        img_id = self.image_infos[idx]
        img_path = os.path.join(self.image_dir, img_id)
        if not os.path.exists(img_path):
            print(f"Image {img_path} not found.")
            return None, None
        img = Image.open(img_path).convert('RGB')
        if self.transform:
            img = self.transform(img)
        data = self.df[self.df['frame'] == img_id]
        boxes = data[['xmin', 'ymin', 'xmax', 'ymax']].values
        labels = data['class_id'].values
        boxes = torch.as_tensor(boxes, dtype=torch.float32)
        labels = torch.as_tensor(labels, dtype=torch.int64)
        target = {'boxes': boxes, 'labels': labels}
        return img, target

transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor()
])

def collate_fn(batch):
    batch = list(filter(lambda x: x[0] is not None, batch))
    return tuple(zip(*batch))

print("Creating Datasets...")
train_ds = SelfDrivingCarDataset(df_train, image_dir, transform)
val_ds = SelfDrivingCarDataset(df_val, image_dir, transform)

print("Loading Datasets...")
train_loader = DataLoader(train_ds, batch_size=10, shuffle=True, collate_fn=collate_fn)
val_loader = DataLoader(val_ds, batch_size=10, shuffle=False, collate_fn=collate_fn)

# Load the YOLO model
yolo_model = YOLO('yolov8m.pt')
yolo_model.dataset = config_file  # Path to your custom dataset YAML file
yolo_model.train(data=config_file, epochs=2, batch=10, imgsz=224)


print("Evaluating Models...")

# Function to evaluate model on a batch of images
def evaluate_model(model, loader, device):
    model.eval()
    results = []
    with torch.no_grad():
        for imgs, targets in loader:
            imgs = [img.to(device) for img in imgs]
            outputs = model.predict(imgs, verbose=False)
            for output in outputs:
                results.append(output)
    return results

print("Move model to device..")
yolo_model.to(device)

def calculate_metrics(results, targets):
    print("Calculating Metrics...")
    # Initialize containers for true positives, false positives, and false negatives
    tp = defaultdict(int)
    fp = defaultdict(int)
    fn = defaultdict(int)

    # Iterate over all results and corresponding targets
    for result, target in zip(results, targets):
        pred_boxes = result.boxes.xyxy.cpu().numpy()
        pred_labels = result.boxes.cls.cpu().numpy()
        pred_scores = result.boxes.conf.cpu().numpy()

        true_boxes = target['boxes'].cpu().numpy()
        true_labels = target['labels'].cpu().numpy()

        for label in set(true_labels).union(set(pred_labels)):
            # Filter predictions and targets by the current label
            pred_indices = pred_labels == label
            true_indices = true_labels == label

            pred_boxes_label = pred_boxes[pred_indices]
            true_boxes_label = true_boxes[true_indices]

            # Calculate the IoU for each predicted and true box pair
            ious = np.zeros((len(pred_boxes_label), len(true_boxes_label)))
            for i, pred_box in enumerate(pred_boxes_label):
                for j, true_box in enumerate(true_boxes_label):
                    ious[i, j] = iou(pred_box, true_box)

            # Determine matches based on IoU threshold
            iou_threshold = 0.5
            matched_pred = set()
            matched_true = set()

            for i, iou_row in enumerate(ious):
                for j, iou_val in enumerate(iou_row):
                    if iou_val >= iou_threshold:
                        matched_pred.add(i)
                        matched_true.add(j)

            # Update counts
            tp[label] += len(matched_pred)
            fp[label] += len(pred_boxes_label) - len(matched_pred)
            fn[label] += len(true_boxes_label) - len(matched_true)

    # Calculate precision, recall, and F1-score for each class
    precisions = {}
    recalls = {}
    f1_scores = {}

    for label in set(tp.keys()).union(fp.keys()).union(fn.keys()):
        precision = tp[label] / (tp[label] + fp[label]) if (tp[label] + fp[label]) > 0 else 0
        recall = tp[label] / (tp[label] + fn[label]) if (tp[label] + fn[label]) > 0 else 0
        f1_score = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0

        precisions[label] = precision
        recalls[label] = recall
        f1_scores[label] = f1_score

    return precisions, recalls, f1_scores

# Define IoU function
def iou(boxA, boxB):
    xA = max(boxA[0], boxB[0])
    yA = max(boxA[1], boxB[1])
    xB = min(boxA[2], boxB[2])
    yB = min(boxA[3], boxB[3])
    interArea = max(0, xB - xA + 1) * max(0, yA - yB + 1)
    boxAArea = (boxA[2] - boxA[0] + 1) * (boxA[3] - boxA[1] + 1)
    boxBArea = (boxB[2] - boxB[0] + 1) * (boxB[3] - boxB[1] + 1)
    iou = interArea / float(boxAArea + boxBArea - interArea)
    return iou

def train_one_epoch(model, optimizer, data_loader, device, epoch, print_freq=10):
    model.train()
    total_loss = 0
    for i, (images, targets) in enumerate(data_loader):
        images = [image.to(device) for image in images]
        targets = [{k: v.to(device) for k, v in t.items()} for t in targets]

        # Clear gradients
        optimizer.zero_grad()

        # Forward pass
        outputs = model(images)
        loss = sum(loss for loss in outputs.values())
        
        # Backward pass
        loss.backward()
        optimizer.step()
        
        total_loss += loss.item()
        
        if i % print_freq == 0:
            print(f'Epoch {epoch}, Batch {i}, Loss: {loss.item()}')

    return total_loss / len(data_loader)

def train_model(model, train_loader, val_loader, device, num_epochs=10, learning_rate=1e-4):
    optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
    
    for epoch in range(num_epochs):
        print(f'Starting epoch {epoch+1}/{num_epochs}')
        train_loss = train_one_epoch(model, optimizer, train_loader, device, epoch)
        print(f'Epoch {epoch+1}, Train Loss: {train_loss}')
        
        if epoch % 1 == 0:  # Change this to 5 or desired value to run validation less frequently
            model.eval()
            results = evaluate_model(model, val_loader, device)
            targets = [{k: v for k, v in t.items()} for _, t in val_loader.dataset]
            precisions, recalls, f1_scores = calculate_metrics(results, targets)
            
            print(f'Epoch {epoch+1}, Validation Metrics:')
            for label in precisions.keys():
                print(f'Class {label}: Precision: {precisions[label]:.4f}, Recall: {recalls[label]:.4f}, F1-Score: {f1_scores[label]:.4f}')

print("Training Model...")
train_model(yolo_model, train_loader, val_loader, device, num_epochs=2)

def display_evaluation_results(results):
    for i, result in enumerate(results):
        print(f"Image {i+1}")
        for box in result.boxes:
            label = result.names[box.cls.item()]
            coordinates = box.xyxy.tolist()
            confidence = round(box.conf.item(), 2)
            print(f"Label: {label}, Confidence: {confidence}, Coordinates: {coordinates}")

print("Evaluate the model on the validation set...")
results = evaluate_model(yolo_model, val_loader, device)

print("Display evaluation results..")
display_evaluation_results(results)
''''